In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np

plt.rcParams.update({'font.size': 20})
title_font_size = 27


In [2]:
def plot_training_results(model_dir, title ="model"):
    """
    plot training results for each run, Epochs and metrics careful noise is not considered
    """
    # list of model folders with results in it
    # for example 11.07_09.41_.glove_d_300.epochs_50.loss_weighted_bce.sgd.lr_005
    l = [elem for elem in os.listdir(model_dir) if not (elem.startswith('C') or elem.startswith('.'))]
    n_cols = 2
    n_rows=len(l)
    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    fig.suptitle(f"{title} - Training Process for different Metrics and Noise Rates", fontsize=40, y=1, weight = 'bold')

    if not isinstance(axs, list):
        axs = axs.flatten()
    idx = 0
    for i, elem in enumerate(l):
        path=model_dir+elem+'/results.csv'
        df = pd.read_csv(path, index_col = False)
        axs[idx].plot(df['epoch'], df['train_maAP']*100, label='train_maAP', linestyle='dotted', c='r')
        axs[idx].plot(df['epoch'], df['train_miAP']*100, label='train_miAP', linestyle='dotted', c='b')
        axs[idx].plot(df['epoch'], df['valid_maAP']*100, label='valid_maAP', linestyle='solid', c='r')
        axs[idx].plot(df['epoch'], df['valid_miAP']*100, label='valid_miAP', linestyle='solid', c='b')

        axs[idx].set_xlabel('epochs', fontsize=title_font_size-2)
        axs[idx].set_ylabel('Metric', fontsize=title_font_size-2)

        axs[idx].yaxis.set_ticks(np.arange(0,101,10))
        axs[idx].xaxis.set_ticks(np.arange(0,51, 5))


        legend = axs[idx].legend(loc='lower right', shadow=True, fontsize='x-large')
        idx += 1

        axs[idx].plot(df['epoch'], df['train_maF1']*100, label='train_maF1', linestyle='dotted', c='r')
        axs[idx].plot(df['epoch'], df['train_miF1']*100, label='train_miF1', linestyle='dotted', c='b')
        axs[idx].plot(df['epoch'], df['valid_maF1']*100, label='valid_maF1', linestyle='solid', c='r')
        axs[idx].plot(df['epoch'], df['valid_miF1']*100, label='valid_miF1', linestyle='solid', c='b')

        axs[idx].set_xlabel('epochs', fontsize=title_font_size-2)
        axs[idx].set_ylabel('Scores', fontsize=title_font_size-2)

        axs[idx].yaxis.set_ticks(np.arange(0,101,10))
        axs[idx].xaxis.set_ticks(np.arange(0,51, 5))
        legend = axs[idx].legend(loc='lower right', shadow=True, fontsize='xx-large')
        idx += 1
    
    for ax, row in zip(axs[::2], ["No Noise", "50% Mix Noise"]):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, col in zip(axs[:2], ["mAP's", "F1 Scores"]):
        ax.set_title(col, fontsize=40,  weight = 'bold')

    plt.tight_layout()
    fig.savefig(f"{model_dir}{title}.png", dpi=300)
    fig.savefig(f"{model_dir}{title}.jpg", dpi=300)

    plt.show()

In [136]:
#path = f"/home/joking/Downloads/results/deepglobe/{m}/"
path = "/home/joking/Downloads/test/"
plot_training_results(path, title="CbMLC")

### Sort directories by noise

In [3]:
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np


In [4]:
def sort_dir_by_noise(dir_path):
    top_dir_list = [elem for elem in os.listdir(dir_path) if not elem.startswith('.')]
    for a_dir in top_dir_list:
        an = "addnoise"
        an_idx =  a_dir.find(an)
        new_dir = a_dir[an_idx:]
        new_name = a_dir[:an_idx]

        source_dir = os.path.join(dir_path, a_dir)

        target_dir = os.path.join(dir_path, new_dir, new_name)
        try:
            os.makedirs(target_dir)
        except OSError as exc:
            pass


        file_names = os.listdir(source_dir)

        for file_name in file_names:
            shutil.move(os.path.join(source_dir, file_name), target_dir)
        os.rmdir(source_dir)


In [5]:
def collect_results(dir_path,root_dir="", model_name=""):
    
    """
    collect results for a model, assumes the runs are already split for noise level ie
    path is: model/addnoise..subnoise.../time ...
    """
    if not root_dir:
        root_dir = dir_path
    noise_d_list = [elem for elem in os.listdir(dir_path) if not elem.startswith('.')]
    results_list = []

    for noise_lvl in noise_d_list:
        model_run_path = os.path.join(dir_path, noise_lvl)
        
        # collect all sub dirs 
        model_run_dirs = [elem for elem in os.listdir(model_run_path) if not elem.startswith('.')]


        for idx, directory in enumerate(model_run_dirs):
            data_list= [model_name]
            index_list = ["Model_Name"]
            # concatenate path
            csv_path = os.path.join(model_run_path, directory, "results.csv")
            tmp_df = pd.read_csv(csv_path, index_col=False)
            
            separate_noise = noise_lvl.split('.')
            for n in separate_noise:
                noise_str,noise_val = n.split('_')
                data_list.append(noise_val)
                index_list.append(noise_str)
                
                
            data_list += directory.split('.')[:-1]
            index_list += ["Time", "dim", 'loss', 'opti', 'lr']

            test_cols= [col for col in tmp_df.columns if col.startswith('test')]
            tmp_df = tmp_df[test_cols]
            
            best_row = tmp_df.iloc[tmp_df['test_maAP'].idxmax()]
            
            final_res= pd.concat([pd.Series(data=data_list, index=index_list)
                                  ,best_row])
            results_list.append(final_res)
        
    df = pd.DataFrame(results_list)
    df['mixnoise'] = np.where( df['addnoise'] == df['subnoise']
                     , df['addnoise'] , 0) # create a mixnoise column when addnoise == subnoise
    df.to_csv(f'{root_dir}/{model_name}_results.csv',  na_rep='NULL', index=False) 
    return df

In [6]:
def plot_results(dir_path="/home/joking/Downloads", models = ['resnet', 'lamp', 'cbmlc'], losses = ['bce', 'asl', 'weighted_bce']):
    
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]
    n_cols = len(losses)
    n_rows= len(models)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    if not isinstance(axs, list):
        axs = axs.flatten()
    idx = 0
    #fig.suptitle("mAP Score for different Models and Loss Functions", fontsize=title_font_size, y=1, weight = 'bold')

    for k, model in enumerate(models):

        model_df = pd.read_csv(f"{dir_path}/{model}_results.csv")
        model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
        model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
        for i, loss in enumerate(losses):
            loss_df = model_df.loc[model_df['loss'] == loss]
            
            # prepare data
            add_noise_df_macro = loss_df.loc[loss_df['subnoise'] == 0]['test_maAP']*100
            sub_noise_df_macro = loss_df.loc[loss_df['addnoise'] == 0]['test_maAP']*100
            mix_noise_df_macro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_maAP']*100
            
            ms = 15# marker size
            axs[idx].plot(ticks, add_noise_df_macro , label='Add Noise', linestyle='solid', c='r', marker='d', markersize=ms)
            axs[idx].plot(ticks, sub_noise_df_macro , label='Sub Noise', linestyle='solid', c='b', marker='o', markersize=ms)
            axs[idx].plot(ticks, mix_noise_df_macro , label='Mix Noise', linestyle='solid', c='black', marker='s', markersize=ms)

            axs[idx].set_xlabel('Noise Level', fontsize=title_font_size-2)
            axs[idx].set_ylabel('macro MAP', fontsize=title_font_size-2)
            # axs[idx].grid(axis="x")
            # axs[idx].grid(axis="y")
            
            axs[idx].yaxis.set_ticks(np.arange(0,101,10))
            axs[idx].xaxis.set_ticks(ticks)
            
            axs[idx].yaxis.set_ticklabels(np.arange(0,101,10), fontsize=title_font_size-2)
            axs[idx].xaxis.set_ticklabels(ticks, fontsize=title_font_size-2)
            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='xx-large')
            
            idx += 1



    for ax, row in zip(axs[::3], models):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, col in zip(axs[:3], losses):
        ax.set_title(col, fontsize=40,  weight = 'bold')

    plt.tight_layout()
    fig.savefig(f"{dir_path}/final_results.png", dpi=300)
    fig.savefig(f"{dir_path}/final_results.jpg", dpi=300)

    plt.show()   

In [156]:
def plot_results_with_miandma(dir_path="/home/joking/Downloads", models = ['resnet'], losses = ['bce', 'weighted_bce']):
    
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]
    n_cols = len(losses)
    n_rows= len(models)*2

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    if not isinstance(axs, list):
        axs = axs.flatten()
    idx = 0
    #fig.suptitle("Resnet mAP Scores for BCE and WBCE", fontsize=title_font_size, y=1, weight = 'bold')

    for k, model in enumerate(models):

        model_df = pd.read_csv(f"{dir_path}/{model}_results.csv")
        model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
        model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
        for i, loss in enumerate(losses):
            loss_df = model_df.loc[model_df['loss'] == loss]
            
            # prepare data
            add_noise_df_macro = loss_df.loc[loss_df['subnoise'] == 0]['test_maAP']*100
            sub_noise_df_macro = loss_df.loc[loss_df['addnoise'] == 0]['test_maAP']*100
            mix_noise_df_macro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_maAP']*100
            
            ms = 15# marker size
            axs[idx].plot(ticks, add_noise_df_macro , label='Add Noise', linestyle='solid', c='r', marker='d', markersize=ms)
            axs[idx].plot(ticks, sub_noise_df_macro , label='Sub Noise', linestyle='solid', c='b', marker='o', markersize=ms)
            axs[idx].plot(ticks, mix_noise_df_macro , label='Mix Noise', linestyle='solid', c='black', marker='s', markersize=ms)

            axs[idx].set_xlabel('Noise Level', fontsize=title_font_size-2)
            axs[idx].set_ylabel('macro MAP', fontsize=title_font_size-2)
            # axs[idx].grid(axis="x")
            # axs[idx].grid(axis="y")
            
            axs[idx].yaxis.set_ticks(np.arange(0,101,10))
            axs[idx].xaxis.set_ticks(ticks)
            
            axs[idx].yaxis.set_ticklabels(np.arange(0,101,10), fontsize=title_font_size-2)
            axs[idx].xaxis.set_ticklabels(ticks, fontsize=title_font_size-2)
            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='xx-large')
            
            ################################### second index
            # prepare data
            add_noise_df_macro = loss_df.loc[loss_df['subnoise'] == 0]['test_miAP']*100
            sub_noise_df_macro = loss_df.loc[loss_df['addnoise'] == 0]['test_miAP']*100
            mix_noise_df_macro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_miAP']*100
            
            ms = 15# marker size
            axs[idx+2].plot(ticks, add_noise_df_macro , label='Add Noise', linestyle='dashed', c='r', marker='d', markersize=ms)
            axs[idx+2].plot(ticks, sub_noise_df_macro , label='Sub Noise', linestyle='dashed', c='b', marker='o', markersize=ms)
            axs[idx+2].plot(ticks, mix_noise_df_macro , label='Mix Noise', linestyle='dashed', c='black', marker='s', markersize=ms)

            axs[idx+2].set_xlabel('Noise Level', fontsize=title_font_size-2)
            axs[idx+2].set_ylabel('micro MAP', fontsize=title_font_size-2)
            # axs[idx].grid(axis="x")
            # axs[idx].grid(axis="y")
            
            axs[idx+2].yaxis.set_ticks(np.arange(0,101,10))
            axs[idx+2].xaxis.set_ticks(ticks)
            
            axs[idx+2].yaxis.set_ticklabels(np.arange(0,101,10), fontsize=title_font_size-2)
            axs[idx+2].xaxis.set_ticklabels(ticks, fontsize=title_font_size-2)
            legend = axs[idx+2].legend(loc='lower left', shadow=True, fontsize='xx-large')
            
            idx += 1



    for ax, row in zip(axs[::2], ["Resnet - macro mAP", "Resnet - micro mAP"]):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, col in zip(axs[:3], losses):
        ax.set_title(col, fontsize=40,  weight = 'bold')

    plt.tight_layout()
    fig.savefig(f"{dir_path}/resnet_comp.png", dpi=300)
    fig.savefig(f"{dir_path}/resnet_comp.jpg", dpi=300)

    plt.show()   

In [141]:
root_path = "/home/joking/Downloads/results/d50"
plot_results_with_miandma(dir_path=root_path)

# Organize

In [11]:
import shutil, os
#################### ############################
models = ['resnet', 'lamp', 'cbmlc']
root_path = "/home/joking/Downloads/d50_3"
for m in models:
    dir_path = f"{root_path}/{m}"

    try:
        # Organize results after noise level
        sort_dir_by_noise(dir_path)
        

    except OSError:
        pass
    df = collect_results(dir_path, model_name=m, root_dir=root_path)

## Average DFs


In [42]:
root_path = "/home/joking/Downloads/all_res"
models = ['resnet', 'lamp', 'cbmlc']
cols_to_avg = ["test_miAP",  "test_maAP",  "test_miF1",  "test_maF1",  "test_loss" ]
dimension_dirs = [elem for elem in os.listdir(root_path) if not elem.startswith('.')]
for model in models:
    avg_list = []
    for dim_dir in dimension_dirs:
        csv_path = os.path.join(root_path, dim_dir, f"{model}_results.csv")
        df = pd.read_csv(csv_path)
        avg_list.append(df)
        
    res_df = avg_list[0].copy(deep=True)
    
    for col in cols_to_avg:
        res_df[col].values[:] = 0
        for df in avg_list:
            res_df[col].values[:] += df[col].values[:]
        res_df[col].values[:] /= 3
        
    df.to_csv(f'{root_path}/{model}_results.csv',  na_rep='NULL', index=False) 
            
        

# Big Plots

In [43]:
root_path = "/home/joking/Downloads/all_res/avg"
plot_results(dir_path=root_path)

# Noise Robustness

In [44]:
def calculate_noise_robustness(noise_series):
    # calculate the percentage value how the score is compared to the score without noise
    noise_series = noise_series / noise_series.iloc[0]
    return noise_series[1:]

# plot noise robustness
def plot_noise_robustness(root_dir = "", losses=["bce", "asl", "weighted_bce"], models = ['resnet', 'cbmlc']):
    
    ticks = [ 0.1, 0.3, 0.5, 0.7]

    n_cols = len(losses)
    n_rows= len(models)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    if not isinstance(axs, list):
        axs = axs.flatten()
    idx = 0
    #fig.suptitle("Noise Robustness for different Models and Loss Functions", fontsize=title_font_size+2, y=1, weight = 'bold')
    for k, model in enumerate(models):

        model_df = pd.read_csv(f"{root_dir}/{model}_results.csv")
        model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
        model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
        for i, loss in enumerate(losses):
            loss_df = model_df.loc[model_df['loss'] == loss]

            add_noise_df_macro = loss_df.loc[loss_df['subnoise'] == 0]['test_maAP']
            sub_noise_df_macro = loss_df.loc[loss_df['addnoise'] == 0]['test_maAP']
            mix_noise_df_macro = loss_df.loc[loss_df['addnoise'] == loss_df['subnoise']]['test_maAP']

            add_noise_df_macro = calculate_noise_robustness(add_noise_df_macro)*100
            sub_noise_df_macro = calculate_noise_robustness(sub_noise_df_macro)*100
            mix_noise_df_macro = calculate_noise_robustness(mix_noise_df_macro)*100       
                        
            ms = 15# marker size
            axs[idx].plot(ticks, add_noise_df_macro , label='Add Noise', linestyle='solid', c='r', marker='d', markersize=ms)
            axs[idx].plot(ticks, sub_noise_df_macro , label='Sub Noise', linestyle='solid', c='b', marker='o', markersize=ms)
            axs[idx].plot(ticks, mix_noise_df_macro , label='Mix Noise', linestyle='solid', c='black', marker='s', markersize=ms)
            

            axs[idx].set_title(f'{loss}', fontsize=title_font_size)
            axs[idx].set_xlabel('Noise Level', fontsize=title_font_size)
            axs[idx].set_ylabel('Percentage decrease of ma MAP ', fontsize=title_font_size)
            #axs[idx].grid(axis="x")
            #axs[idx].grid(axis="y")
            y_ticks = [f"{x}%" for x in range(0,101,10)]
            axs[idx].yaxis.set_ticks(np.arange(0,101,10), y_ticks)
            axs[idx].xaxis.set_ticks(ticks)
            
            axs[idx].yaxis.set_ticklabels(y_ticks, fontsize=title_font_size-2)
            axs[idx].xaxis.set_ticklabels(ticks, fontsize=title_font_size-2)
            
            
            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='xx-large')
            idx += 1


        
    for ax, row in zip(axs[::3], models):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, col in zip(axs[:3], losses):
        ax.set_title(col, fontsize=40,  weight = 'bold')

    plt.tight_layout()
    plt.show()
    fig.savefig(f"{root_dir}/noise_robustness.png", dpi=300)
    fig.savefig(f"{root_dir}/noise_robustness.jpg", dpi=300)


In [45]:
root_path = "/home/joking/Downloads/all_res/avg"

plot_noise_robustness(root_dir=root_path)

In [46]:
def plot_specific_loss_for_noise_comparison(root_dir="", losses= ["bce", 'asl', 'weighted_bce'], models = ['resnet', 'lamp', 'cbmlc']):
    
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]
    noises = ['addnoise', 'subnoise', 'mixed']
    n_cols = len(noises)
    n_rows= len(losses)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    if not isinstance(axs, list):
        axs = axs.flatten()
    #fig.suptitle(f"Each Noisetype compared to each Model for each Loss", fontsize=title_font_size, y=1, weight = 'bold')
    

    idx = 0
    for loss in losses:
        # setup the dataframes for each loss
        model_dfs = []
        for model in models:
            model_df = pd.read_csv(f"{root_dir}/{model}_results.csv")
            model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
            model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
            model_df = model_df.loc[model_df['loss'] == loss]
            model_dfs.append(model_df)
        rn_df = model_dfs[0]
        lamp_df = model_dfs[1]
        cb_df  = model_dfs[2]
        
        #iterate oover noises
        for noise in (noises):

            if noise == 'mixed':
                rn_noise = rn_df.loc[rn_df['addnoise'] == rn_df['subnoise']]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['addnoise'] == lamp_df['subnoise']]['test_maAP']
                cb_noise = cb_df.loc[cb_df['addnoise'] == cb_df['subnoise']]['test_maAP']


            elif noise=="subnoise":
                rn_noise = rn_df.loc[rn_df['addnoise'] == 0]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['addnoise'] == 0]['test_maAP']
                cb_noise = cb_df.loc[cb_df['addnoise'] == 0]['test_maAP']
            else:
                rn_noise = rn_df.loc[rn_df['subnoise'] == 0]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['subnoise'] == 0]['test_maAP']
                cb_noise = cb_df.loc[cb_df['subnoise'] == 0]['test_maAP']



            ms = 15# marker size
            axs[idx].plot(ticks, rn_noise*100 , label=f'Resnet', linestyle='solid', c='c', marker='d', markersize=ms)
            axs[idx].plot(ticks, lamp_noise*100 , label=f'Lamp', linestyle='solid', c='m', marker='o', markersize=ms)
            axs[idx].plot(ticks, cb_noise*100 , label=f' CBMLC', linestyle='solid', c='y', marker='s', markersize=ms)

            axs[idx].set_xlabel('Noise Level', fontsize=title_font_size-2)
            axs[idx].set_ylabel('macro MAP', fontsize=title_font_size-2)
            # axs[idx].grid(axis="x")
            # axs[idx].grid(axis="y")
            
            axs[idx].yaxis.set_ticks(np.arange(0,101,10))
            axs[idx].xaxis.set_ticks(ticks)
            
            axs[idx].yaxis.set_ticklabels(np.arange(0,101,10), fontsize=title_font_size-2)
            axs[idx].xaxis.set_ticklabels(ticks, fontsize=title_font_size-2)

            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='xx-large')
            idx += 1
    
    for ax, row in zip(axs[::3], losses):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, row in zip(axs[:3], noises):
        ax.set_title(row, fontsize=40,  weight = 'bold')


    plt.tight_layout()
    plt.show()
    fig.savefig(f"{root_dir}/noise_type_zoomin.png", dpi=300)
    fig.savefig(f"{root_dir}/noise_type_zoomin.jpg", dpi=300)



In [47]:
root_path = "/home/joking/Downloads/all_res/avg"


plot_specific_loss_for_noise_comparison(root_path, losses = ['asl', 'bce'])

# Create one big dataframe

In [48]:
import numpy as np


def combine_all_res_dfs(root_dir,  models = ['resnet', 'lamp', 'cbmlc']):

    dim_dir_list = [elem for elem in os.listdir(root_dir) if not (elem.startswith('.')or elem.startswith('plots') or elem.startswith('all_res'))]
    print(dim_dir_list)
    results_df = pd.DataFrame()
    for dim_dir in dim_dir_list:
        dim_path = os.path.join(root_dir, dim_dir) 
        for model in models:
            model_df = pd.read_csv(f"{dim_path}/{model}_results.csv")
            cb_noise = model_df.loc[model_df['addnoise'] == model_df['subnoise']]
            
            model_df['mixnoise'] = np.where( model_df['addnoise'] == model_df['subnoise']
                     , model_df['addnoise'] , 0) # create a mixnoise column when addnoise == subnoise
            model_df = model_df.reset_index(drop=True)

            results_df = pd.concat([results_df, model_df], axis=0)
    results_df.to_csv(f'{root_dir}/all_results.csv',  na_rep='NULL', index=False) 
    return results_df

In [49]:
root_dir = "/home/joking/Downloads/all_res/avg"
results_df =  combine_all_res_dfs(root_dir)
results_df.columns

['cbmlc_results.csv', 'lamp_results.csv', 'resnet_results.csv', 'final_results.png', 'final_results.jpg', 'noise_robustness.png', 'noise_robustness.jpg', 'noise_type_zoomin.png', 'noise_type_zoomin.jpg']


NotADirectoryError: [Errno 20] Not a directory: '/home/joking/Downloads/all_res/avg/cbmlc_results.csv/resnet_results.csv'

In [ ]:
def plot_dimensions(df, model="cbmlc", noises = ['addnoise', 'subnoise', 'mixnoise'], losses= ['asl']):
    """
    plot comparision of the maps of the dim column against each other
    """
    # prepare df
    df = df.drop(columns=["Time", "opti", "lr", "test_miF1", "test_maF1", "test_loss", "test_miAP"]) # drop unnecessary cols
    df = df.loc[df['Model_Name'] == model] # only for one model ( not resnet as it has no dim)
    
    
    all_dims = df['dim'].unique()
    all_colors = ['c', 'm', 'y', 'g', 'b']
    all_markers = ['d', 'o', 's', '*']
    colors = all_colors[:len(all_dims)]
    markers = all_markers[:len(all_dims)]
    
    #prepare plot
    ticks = [0.0, 0.1, 0.3, 0.5, 0.7]
    n_cols = len(noises)
    n_rows= len(losses)
    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    if not isinstance(axs, list):
        axs = axs.flatten()
    idx = 0
    #fig.suptitle(f"Noises compared for different Latent Space dimensions", fontsize=title_font_size, y=1, weight = 'bold')
    
    # outer  y axis
    for loss in losses:
        loss_df = df[df["loss"] == loss]
        
        #outer x axis
        for noise in noises:
            
            if noise == 'mixnoise':
                noise_df = loss_df[loss_df['addnoise'] == loss_df['subnoise']]
                
            elif noise=="subnoise":
                noise_df = loss_df[loss_df['addnoise'] == 0]
                
            else:
                noise_df = loss_df[loss_df['subnoise'] == 0]
            
            for dim, m, c in zip(all_dims, markers, colors):
                data = noise_df[noise_df['dim'] == dim]['test_maAP']*100
                axs[idx].plot(ticks, data , label=f'{dim}', linestyle='solid', c=c, marker=m, markersize=15)
        
        
            axs[idx].set_title(f'{noise}', fontsize=title_font_size)
            axs[idx].set_xlabel('Noise Level', fontsize=title_font_size)
            axs[idx].set_ylabel('macro MAP', fontsize=title_font_size)
            # axs[idx].grid(axis="x")
            # axs[idx].grid(axis="y")
            
            axs[idx].yaxis.set_ticks(np.arange(0,101,10))
            axs[idx].xaxis.set_ticks(ticks)
            
            axs[idx].yaxis.set_ticklabels(np.arange(0,101,10), fontsize=title_font_size)
            axs[idx].xaxis.set_ticklabels(ticks, fontsize=title_font_size)

            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='xx-large')
            idx += 1
                
            

    for ax, row in zip(axs[::3], losses):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, row in zip(axs[:3], noises):
        ax.set_title(row, fontsize=40,  weight = 'bold')


    plt.tight_layout()
    plt.show()
    fig.savefig(f"{root_dir}/plots/noise_type_dimension.png", dpi=300)
    fig.savefig(f"{root_dir}/plots/noise_type_dimension.jpg", dpi=300)




In [ ]:
plot_dimensions(results_df)


In [ ]:
def calculate_noise_robustness(noise_series):
    # calculate the percentage value how the score is compared to the score without noise
    noise_series = noise_series / noise_series.iloc[0]
    return noise_series[1:]

def plot_noisetype_robustness(root_dir="", losses= ["bce", 'asl', 'weighted_bce'], models = ['resnet', 'lamp', 'cbmlc']):
    
    ticks = [ 0.1, 0.3, 0.5, 0.7]
    noises = ['addnoise', 'subnoise', 'mixed']
    n_cols = len(noises)
    n_rows= len(losses)

    fig, axs = plt.subplots(n_rows,n_cols, figsize=(n_cols*15 ,n_rows*10), dpi=300)
    if not isinstance(axs, list):
        axs = axs.flatten()
    #fig.suptitle("Noise Robustness for different Models and Loss Functions", fontsize=title_font_size+2, y=1, weight = 'bold')
    

    idx = 0
    for loss in losses:
        # setup the dataframes for each loss
        model_dfs = []
        for model in models:
            model_df = pd.read_csv(f"{root_dir}/{model}_results.csv")
            model_df = model_df.drop(columns=["Time", "dim", "opti", "lr", "test_miF1", "test_maF1", "test_loss"])
            model_df = model_df.sort_values(by=['addnoise', 'subnoise'])
            model_df = model_df.loc[model_df['loss'] == loss]
            model_dfs.append(model_df)
        rn_df = model_dfs[0]
        lamp_df = model_dfs[1]
        cb_df  = model_dfs[2]
        
        #iterate oover noises
        for noise in (noises):

            if noise == 'mixed':
                rn_noise = rn_df.loc[rn_df['addnoise'] == rn_df['subnoise']]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['addnoise'] == lamp_df['subnoise']]['test_maAP']
                cb_noise = cb_df.loc[cb_df['addnoise'] == cb_df['subnoise']]['test_maAP']


            elif noise=="subnoise":
                rn_noise = rn_df.loc[rn_df['addnoise'] == 0]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['addnoise'] == 0]['test_maAP']
                cb_noise = cb_df.loc[cb_df['addnoise'] == 0]['test_maAP']
            else:
                rn_noise = rn_df.loc[rn_df['subnoise'] == 0]['test_maAP'] 
                lamp_noise = lamp_df.loc[lamp_df['subnoise'] == 0]['test_maAP']
                cb_noise = cb_df.loc[cb_df['subnoise'] == 0]['test_maAP']
            
            rn_noise = calculate_noise_robustness(rn_noise)
            lamp_noise = calculate_noise_robustness(lamp_noise)
            cb_noise = calculate_noise_robustness(cb_noise)

    
            ms = 15# marker size
            axs[idx].plot(ticks, rn_noise*100 , label=f'Resnet', linestyle='solid', c='c', marker='d', markersize=ms)
            axs[idx].plot(ticks, lamp_noise*100 , label=f'Lamp', linestyle='solid', c='m', marker='o', markersize=ms)
            axs[idx].plot(ticks, cb_noise*100 , label=f' CBMLC', linestyle='solid', c='y', marker='s', markersize=ms)

            axs[idx].set_title(f'{loss}', fontsize=title_font_size)
            axs[idx].set_xlabel('Noise Level', fontsize=title_font_size)
            axs[idx].set_ylabel('Percentage decrease of ma MAP ', fontsize=title_font_size)
            #axs[idx].grid(axis="x")
            #axs[idx].grid(axis="y")
            y_ticks = [f"{x}%" for x in range(0,101,10)]
            axs[idx].yaxis.set_ticks(np.arange(0,101,10), y_ticks)
            axs[idx].xaxis.set_ticks(ticks)
            
            axs[idx].yaxis.set_ticklabels(y_ticks, fontsize=title_font_size-2)
            axs[idx].xaxis.set_ticklabels(ticks, fontsize=title_font_size-2)
            
            
            legend = axs[idx].legend(loc='lower left', shadow=True, fontsize='xx-large')
            idx += 1
    
    for ax, row in zip(axs[::3], losses):
        ax.set_ylabel(row, fontsize=40,  weight = 'bold')
        
    for ax, row in zip(axs[:3], noises):
        ax.set_title(row, fontsize=40,  weight = 'bold')


    plt.tight_layout()
    plt.show()
    fig.savefig(f"{root_dir}/noise_type_robustness.png", dpi=300)
    fig.savefig(f"{root_dir}/noise_type_robustness.jpg", dpi=300)



In [ ]:
root_path = "/home/joking/Downloads/all_res/avg"


plot_noisetype_robustness(root_path, losses = ['asl', 'bce'])